In [1]:
# importing libraries 
import sys
from dotenv import load_dotenv
import pandas as pd
sys.path.insert(1, '/home/jabez/week_11/Contract-Advisor-RAG')
load_dotenv()
sys.path.insert(1, '/home/jabez/rizzbuzz with poetry/RAG-Optimization-System/scripts')
import file_loader 
import pipelines 
import evaluation

/home/jabez/rizzbuzz with poetry/RAG-Optimization-System/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Loading data
file_path = '/home/jabez/rizzbuzz with poetry/RAG-Optimization-System/data/cnn_dailymail_3.0.0.csv'
data = file_loader.load_csv(file_path)

In [4]:
# Data overview
df = pd.read_csv('/home/jabez/rizzbuzz with poetry/RAG-Optimization-System/data/cnn_dailymail_3.0.0.csv')
df['highlights'][0]

'Zully Broussard decided to give a kidney to a stranger .\nA new computer program helped her donation spur transplants for six kidney patients .'

In [5]:
data

[Document(metadata={'source': 'Zully Broussard decided to give a kidney to a stranger .\nA new computer program helped her donation spur transplants for six kidney patients .', 'row': 0}, page_content='article: (CNN)Share, and your gift will be multiplied. That may sound like an esoteric adage, but when Zully Broussard selflessly decided to give one of her kidneys to a stranger, her generosity paired up with big data. It resulted in six patients receiving transplants. That surprised and wowed her. "I thought I was going to help this one person who I don\'t know, but the fact that so many people can have a life extension, that\'s pretty big," Broussard told CNN affiliate KGO. She may feel guided in her generosity by a higher power. "Thanks for all the support and prayers," a comment on a Facebook page in her name read. "I know this entire journey is much bigger than all of us. I also know I\'m just the messenger." CNN cannot verify the authenticity of the page. But the power that multip

In [6]:
# Data splitting using RecursiveCharacterTextSplitter
from langchain_text_splitters import RecursiveCharacterTextSplitter
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)
splits = text_splitter.split_documents(data)
splits

[Document(metadata={'source': 'Zully Broussard decided to give a kidney to a stranger .\nA new computer program helped her donation spur transplants for six kidney patients .', 'row': 0}, page_content='article: (CNN)Share, and your gift will be multiplied. That may sound like an esoteric adage, but when Zully Broussard selflessly decided to give one of her kidneys to a stranger, her generosity paired up with big data. It resulted in six patients receiving transplants. That surprised and wowed her. "I thought I was going to help this one person who I don\'t know, but the fact that so many people can have a life extension, that\'s pretty big," Broussard told CNN affiliate KGO. She may feel guided in her generosity by a higher power. "Thanks for all the support and prayers," a comment on a Facebook page in her name read. "I know this entire journey is much bigger than all of us. I also know I\'m just the messenger." CNN cannot verify the authenticity of the page. But the power that multip

In [7]:
# length of the splits
len(splits)

6025

In [3]:
# Storing the splits in a Chroma vectorstore
vectorstore_character = file_loader.character_text_splitter(data)

In [10]:
# Testing simple_pipeline using a question
question = '"who selflessly decided to give one of her kidneys to a stranger?"'
answer = pipelines.simple_pipeline(vectorstore_character, question)
print(answer)

Zully Broussard


In [15]:
file_path = '/home/jabez/rizzbuzz with poetry/RAG-Optimization-System/test_data/syntetic_test_data.csv'
evaluation.generate_syntetic_testdata(data, file_path)

Filename and doc_id are the same for all nodes.                     
Generating:  90%|█████████ | 9/10 [00:46<00:07,  7.14s/it]

In [4]:
syntetic_test_data = pd.read_csv('/home/jabez/rizzbuzz with poetry/RAG-Optimization-System/test_data/syntetic_test_data.csv')

In [5]:
retriver = vectorstore_character.as_retriever(search_type="similarity", search_kwargs={"k": 6})


In [6]:
file_path_with_answer = '/home/jabez/rizzbuzz with poetry/RAG-Optimization-System/test_data/syntetic_test_data_with_answer.csv'
syntetic_test_data_with_answer = evaluation.adding_answer_to_testdata(syntetic_test_data, pipelines.simple_pipeline, vectorstore_character, retriver, file_path_with_answer)

/home/jabez/rizzbuzz with poetry/RAG-Optimization-System/.venv/lib/python3.10/site-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The method `BaseRetriever.get_relevant_documents` was deprecated in langchain-core 0.1.46 and will be removed in 0.3.0. Use invoke instead.
  warn_deprecated(
Creating CSV from Arrow format: 100%|██████████| 1/1 [00:00<00:00, 95.39ba/s]


In [7]:
syntetic_test_data_with_answer = pd.read_csv('/home/jabez/rizzbuzz with poetry/RAG-Optimization-System/test_data/syntetic_test_data_with_answer.csv')

In [7]:
simple_rag_evaluation_result = evaluation.ragas_evaluator(syntetic_test_data_with_answer)

Evaluating: 100%|██████████| 36/36 [00:23<00:00,  1.56it/s]


In [8]:
simple_rag_evaluation_result

question  \
0  What are some reasons why churches do not carb...   
1  How do fans of Supreme Court Justice Ruth Bade...   
2  What role do Shia militias play in the fight a...   
3  How has Valparaiso's success in the tournament...   
4  Who is Parisa Tabriz and what is her role at G...   
5  What was Ben Ferguson's argument about rappers...   
6  What are the additional factors proposed for t...   
7  What challenges does Amran Abdundi face in her...   
8  How do fans of Supreme Court Justice Ruth Bade...   

                                              answer  \
0  Some reasons why churches do not carbon date r...   
1  Fans of Supreme Court Justice Ruth Bader Ginsb...   
2  Shia militias play a significant role in the f...   
3  Valparaiso's success in the tournament has led...   
4  Parisa Tabriz is the 31-year-old computer whiz...   
5  Ben Ferguson's argument was that rappers are a...   
6  The additional factors proposed for the Buddy ...   
7  Amran Abdundi faces challenges such as the ong...   
8  Fans of Supreme Court Justice Ruth Bader Ginsb...   

                                            contexts  \
0  [being carbon dated and there are a few reason...   
1  [article: (CNN)It's no secret that Supreme Cou...   
2  [analyst. "The Iranians are smart enough to kn...   
3  [scouts attending his games, being drafted by ...   
4  [highlights: Parisa Tabriz is the 31-year-old ...   
5  [article: (CNN)Things got testy on "CNN Tonigh...   
6  [highlights: Don McLean: It's bad idea for NTS...   
7  [article: London, England (CNN)Along the dange...   
8  [article: (CNN)It's no secret that Supreme Cou...   

                                        ground_truth  context_precision  \
0  Carbon dating is expensive and most churches d...           0.926667   
1  Fans of Supreme Court Justice Ruth Bader Ginsb...           1.000000   
2  Shia militias play a significant role in the f...           1.000000   
3  Valparaiso's success in the tournament has imp...           1.000000   
4  Parisa Tabriz is a 31-year-old computer whizz ...           1.000000   
5  Ben Ferguson argued that rappers are afraid th...           1.000000   
6  The additional factors proposed for the Buddy ...           1.000000   
7  Amran Abdundi faces numerous challenges in her...           1.000000   
8  Fans of Supreme Court Justice Ruth Bader Ginsb...           1.000000   

   faithfulness  answer_relevancy  context_recall  
0           1.0          0.000000             1.0  
1           1.0          1.000000             1.0  
2           1.0          0.900197             1.0  
3           0.6          0.945975             1.0  
4           1.0          0.981642             1.0  
5           1.0          0.973895             1.0  
6           1.0          0.932058             1.0  
7           1.0          0.950915             1.0  
8           1.0          1.000000             1.0